# Build static feature file

In [17]:
# libraries
import pandas as pd
import boto3
import geopy
from geopy.distance import distance
import warnings
warnings.filterwarnings('ignore')

In [2]:
# define bounding box
UP_LEFT = (38.008050, -122.536985)    
UP_RIGHT = (38.008050, -122.186437)   
DOWN_RIGHT = (37.701933, -122.186437) 
DOWN_LEFT = (37.701933, -122.536985) 

In [3]:
# MAYBE DON'T RELY ON A CSV
# load in the grid from csv file
vsensors_df = pd.read_csv('./data/500m_grid.csv')

In [4]:
# MAYBE DON'T RELY ON A CSV
# get elevations from csv file and merge into dataframe
def getElevations(data_df, filename):
    """
    This function takes as input a dataframe with latitutes and longitudes and 
    the filepath to a csv file with the same latitudes and longitudes and elevations.
    It returns a dataframe that includes the elevations. 
    """
    
    elev_df = pd.read_csv(filename, header='infer')
    elev_df = elev_df[['x','y','elevation']]
    
    data_df = pd.merge(data_df, elev_df)
    if data_df.elevation.isna().sum() > 0:
        print("Error. Not all elevations were found.")
    
    return(data_df)

vsensors_df = getElevations(vsensors_df, './data/grid_elevations.csv')

# set a few grid points at seashore and read from TIF as ocean to 0
vsensors_df.elevation.replace(-32768, 0, inplace=True)

In [5]:
# remove virtual sensors that are in water
vsensors_df = vsensors_df[vsensors_df.in_water == False]

In [6]:
# MAYBE DON'T RELY ON A CSV
# add NDVI vegetation data
vsensors_df.head()

min_lat    max_lat     min_lon     max_lon  x   y  center_lat  \
0  37.822662  37.826210 -122.536985 -122.532493  0  34   37.824436   
1  37.826210  37.829757 -122.536985 -122.532493  0  35   37.827984   
2  37.829757  37.833305 -122.536985 -122.532493  0  36   37.831531   
3  37.833305  37.836852 -122.536985 -122.532493  0  37   37.835079   
4  37.836852  37.840400 -122.536985 -122.532493  0  38   37.838626   

   center_lon  in_water  ndvi  elevation  
0 -122.534739     False -2000         17  
1 -122.534739     False -2000          0  
2 -122.534739     False -2000          0  
3 -122.534739     False  5159         55  
4 -122.534739     False  7053        132

In [7]:
def calc_distance(origin, destination):
    """
    Input: two tuples, each containing (lat, lon)
    Output: distance between the two coordinates in kilometers
    """

    origin = geopy.point.Point(origin)
    destination = geopy.point.Point(destination)
    distance = geopy.distance.distance(origin, destination).km

    return distance

In [8]:
# CURRENTLY THIS TAKES 50 MINUTES. SPEED UP WITH LAMBDAS POSSIBLE?
# for each virtual sensor, find k closest
getreading_df = pd.read_json(path_or_buf="https://www.purpleair.com/json") # get fresh data from purple air
k = 5 

# reduce data to what we need
rsensors_df = pd.DataFrame.from_records(getreading_df.results)
rsensors_df = rsensors_df[['ID', 'Lat', 'Lon']]
rsensors_df = rsensors_df[(rsensors_df.Lat <= UP_LEFT[0]) & (rsensors_df.Lat >= DOWN_LEFT[0]) & 
                    (rsensors_df.Lon >= UP_LEFT[1]) & (rsensors_df.Lon <= UP_RIGHT[1])] # just keep sensors in bounding box
rsensors_df['coords'] = list(zip(rsensors_df.Lat, rsensors_df.Lon))

# remove all the double entries for sensors
rsensors_df.drop_duplicates(subset ="coords", inplace = True) 

# build dataframe of distances between real and virtual sensors
empty_col = [100000] * len(rsensors_df) # put out of bounds large value in new empty column
for row in range(len(vsensors_df)):
    col_name = (vsensors_df.iloc[row].center_lat, vsensors_df.iloc[row].center_lon)
    col_name = str(col_name)
    rsensors_df[col_name] = empty_col

for grid_coord in rsensors_df.columns[4:]:
    for sensor_coord in rsensors_df.coords:
        distance = calc_distance(tuple(float(s) for s in grid_coord.strip("()").split(",")), sensor_coord)
        rsensors_df[grid_coord][rsensors_df.coords == sensor_coord] = distance

# get k-NN sensor IDs
kNN_list = []
for grid_coord in rsensors_df.columns[4:]:
    temp_df = rsensors_df[['ID', grid_coord]]
    temp_df.sort_values(by=[grid_coord], axis=0, ascending=True, inplace=True)
    kNN_list.append(list(temp_df.ID[0:k]))
vsensors_df['NN_list'] = kNN_list

/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: Se

/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: Se

/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: Se

/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: Se

/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: Se

...

/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: Se

/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: Se

/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: Se

/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: Se

/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:26: Se

In [11]:
# add closest epa sensor

# Read historical epa data from s3
bucket = "capstone-air-pollution"
file_name = "EPA/historical_PM25.csv"  # historical
s3 = boto3.client('s3') 
obj = s3.get_object(Bucket= bucket, Key= file_name) 
epa_df = pd.read_csv(obj['Body']) 

#either use site_name or full_aqs_code... confirm that full_aqs_code is a unique, numeric id for station

epa_dict = {}
for station in epa_df.SiteName.unique():
    row = epa_df[epa_df.SiteName == station].iloc[0]
    epa_dict[station] = (row.Latitude, row.Longitude)

closest_epa = []
for vsensor in range(len(vsensors_df)):
    v_coords = (vsensors_df.iloc[vsensor].center_lat, vsensors_df.iloc[vsensor].center_lon)
    nn_distance = 0
    nn_station = ""
    for station in epa_dict.keys():
        distance = calc_distance(epa_dict[station], v_coords)
        if (nn_station == "" or nn_distance > distance):
            nn_distance = distance
            nn_station = station
    closest_epa.append(nn_station)

vsensors_df['closest_epa'] = closest_epa

# this is very fast, but as a lambda:
# vsensor['closest_epa'] = vsensors_df.apply(lambda x: closest_epa(x), axis=1)
# [bay_and_ocean.contains(pt) for pt in boxes_as_points]

In [16]:
# add closest noaa sensor

# read in all ASOS stations w/ lat lon info
filepath = "ftp://ftp.ncdc.noaa.gov/pub/data/noaa/isd-history.txt"
stations = [] # an array of each read line
for station in pd.read_csv(filepath_or_buffer=filepath , encoding='utf-8', chunksize=1):
    stations.append(station.iloc[0,0])

# parse ugly text file to dataframe    
station_cols = ['usaf','wban_number','descriptor', 'lat','lon','elev_m','begin_date','end_date']
stations = stations[17:] # remove header (meta data and column names)
station_data = [] # an array of arrays, inner arrays are all data for one record, outer array is all records
for station in stations:
    print(station)
    data_start = 0 # position after awk location data in each record
    USAF = station[0:6]
    WBAN = station[7:12]
    data_start = station.find('+')
    location_string = station[12:data_start]
    rest_of_data = station[data_start:].split()  
    station_record = [USAF, WBAN, location_string] + rest_of_data
    station_data.append(station_record)
NOAA_df = pd.DataFrame(station_data, columns = station_cols)

# keep on the current Bay Area sensors
NOAA_df = NOAA_df.astype({'lat': float, 'lon': float, 'wban_number': int, 'end_date': str})
NOAA_df = NOAA_df[(NOAA_df.lat <= UP_LEFT[0]) & (NOAA_df.lat >= DOWN_LEFT[0]) & 
                    (NOAA_df.lon >= UP_LEFT[1]) & (NOAA_df.lon <= UP_RIGHT[1])] # just keep sensors in bounding box
NOAA_df = NOAA_df[(NOAA_df.end_date.str.contains("2019")) or (NOAA_df.end_date.str.contains("2020"))] # just get current sensors, sorta

NOAA_dict = {}
for station in NOAA_df.wban_number.unique():
    row = NOAA_df[NOAA_df.wban_number == station].iloc[0]
    NOAA_dict[station] = (row.lat, row.lon)

closest_NOAA = []
for vsensor in range(len(vsensors_df)):
    v_coords = (vsensors_df.iloc[vsensor].center_lat, vsensors_df.iloc[vsensor].center_lon)
    nn_distance = 0
    nn_station = ""
    for station in NOAA_dict.keys():
        distance = calc_distance(NOAA_dict[station], v_coords)
        if (nn_station == "" or nn_distance > distance):
            nn_distance = distance
            nn_station = station
    closest_NOAA.append(nn_station)

vsensors_df['closest_NOAA'] = closest_NOAA


007018 99999 WXPOD 7018                                  +00.000 +000.000 +7018.0 20110309 20130730
007026 99999 WXPOD 7026                    AF            +00.000 +000.000 +7026.0 20120713 20170822
007070 99999 WXPOD 7070                    AF            +00.000 +000.000 +7070.0 20140923 20150926
008260 99999 WXPOD8270                                   +00.000 +000.000 +0000.0 20050101 20100920
008268 99999 WXPOD8278                     AF            +32.950 +065.567 +1156.7 20100519 20120323
008307 99999 WXPOD 8318                    AF            +00.000 +000.000 +8318.0 20100421 20100421
008411 99999 XM20                                                                 20160217 20160217
008414 99999 XM18                                                                 20160216 20160217
008415 99999 XM21                                                                 20160217 20160217
008418 99999 XM24                                                                 20160217 20160217


083910 99999 SEVILLA                       SP      LEZL  +37.418 -005.893 +0033.8 19730101 20191110
083970 99999 MORON AB                      SP      LEMO  +37.175 -005.616 +0086.9 19580102 20191110
084100 99999 CORDOBA                       SP      LEBA  +37.842 -004.849 +0090.5 19730101 20191110
084170 99999 JAEN                          SP            +37.783 -003.817 +0580.0 19730201 20191108
084190 99999 GRANADA                       SP      LEGR  +37.189 -003.777 +0566.9 19730101 20191110
084200 99999 GRANADA / ARMILLA             SP            +37.133 -003.617 +0717.0 19730101 20040108
084290 99999 ALCANTARILLA                  SP      LERI  +37.951 -001.230 +0076.2 19730101 20191110
084300 99999 MURCIA                        SP            +38.000 -001.167 +0062.0 19730101 20191110
084310 99999 CASTILLO GALERAS              SP            +37.583 -001.000 +0217.0 19730101 20040805
084330 99999 MURCIA SAN JAVIER             SP      LELC  +37.775 -000.812 +0003.4 19730101 20191110


247390 99999 CHAINGDA                      RS            +62.283 +119.850 +0308.2 19590101 20150407
247530 99999 NAMTSY                        RS            +62.733 +129.667 +0089.8 19690101 20191110
247580 99999 BERDIGESTYAH                  RS            +62.267 +127.067 +0231.4 19590101 20191110
247610 99999 BOROGONCY                     RS            +62.667 +131.133 +0140.0 19600113 19810411
247630 99999 KREST-HAL' DZHAY              RS            +62.817 +134.433 +0114.5 19590101 20191110
247660 99999 YTYK-KJUEL                    RS            +62.467 +133.417 +0120.0 19590101 20020703
247680 99999 CURAPCA                       RS            +62.033 +132.600 +0186.0 19480101 20191110
247710 99999 TEPLY KLJUCH                  RS            +62.783 +136.850 +0288.6 19590101 20191110
247840 99999 MUSKHAYA                      RS            +62.600 +140.700 +2149.0 19590101 19631231
247900 99999 SUSUMAN                       RS            +62.783 +148.167 +0655.0 19590901 20191110


408510 99999 SIRJAN                        IR            +29.467 +055.717 +1739.0 19890101 20191110
408530 99999 BAFT                          IR            +29.233 +056.567 +2280.0 19490108 20191110
408540 99999 BAM                           IR      OIKM  +29.084 +058.450 +0940.0 19660101 20191110
408560 99999 ZAHEDAN INTL                  IR      OIZH  +29.476 +060.907 +1377.7 19570701 20191110
408570 99999 BUSHEHR                       IR            +28.950 +050.850 +0008.0 19961201 20171231
408580 99999 BUSHEHR                       IR      OIBB  +28.945 +050.835 +0020.7 19440101 20191110
408590 99999 FASA                          IR      OISF  +28.892 +053.723 +1298.8 19730101 20191110
408690 99999 FARSI ISLAND                  IR            +27.983 +050.183 +0004.0 19751101 20111222
408720 99999 BANDAR-E-DAYYER               IR            +27.833 +051.933 +0004.0 20060913 20191110
408750 99999 BANDAR ABBASS INTL            IR      OIKB  +27.218 +056.378 +0006.7 19650106 20191110


576230 99999 CHEN-NAN                      CH            +00.000 +000.000 -0999.0 19740425 20020410
576320 99999 CHANG-PU-QI                   CH            +00.000 +000.000 -0999.0 19740421 20020622
576330 99999 YOUYANG                       CH            +28.833 +108.767 +0665.0 19560820 20191110
576450 99999 HUA-YUAN                      CH            +00.000 +000.000 -0999.0 19740425 20020406
576460 99999 APPROXIMATE LOCALE            CH            +28.500 +109.833 +0000.0 19740423 20020927
576490 99999 QIAN-ZHOU-ZHEN                CH            +28.267 +109.683 +0560.0 19600101 20100424
576530 99999 BOGUS CHINESE                 CH            +00.000 +000.000 -0999.0 19740421 19840602
576550 99999 YUANLING                      CH            +28.467 +110.400 +0143.0 19560820 20191110
576590 99999 APPROXIMATE LOCALE            CH            +28.167 +110.967 +0000.0 19740421 20020809
576620 99999 CHANGDE                       CH            +29.050 +111.683 +0035.0 19560820 20191110


703057 26653 TOKSOOK BAY AIRPORT           US   AK PAOO  +60.541 -165.087 +0018.0 20060101 20191111
703057 99999 TOOKSOK BAY                   US   AK PAOO  +60.533 -165.083 +0021.0 20050929 20051231
703058 00110 NELSON LAGOON AIRPORT         US   AK PAOU  +56.017 -161.167 +0004.3 20050930 20191111
703058 99999 NELSON LAGOON                 US   AK PAOU  +56.010 -161.160 +0004.0 20080101 20180514
703059 99999 KING COVE                     US   AK PAVC  +55.170 -162.270 +0047.0 20050930 20191110
703061 25521 IGIUGIG AIRPORT               US   AK PAIG  +59.324 -155.902 +0027.4 20060101 20191022
703061 99999 IGIUGIG                       US   AK PAIG  +59.300 -155.900 +0027.0 20050929 20051231
703080 25713 ST PAUL ISLAND AIRPORT        US   AK PASN  +57.155 -170.222 +0010.7 19431105 20191111
703160 25624 COLD BAY AIRPORT              US   AK PACD  +55.221 -162.732 +0023.8 19420304 20191111
703165 25617 SAND POINT AIRPORT            US   AK PASD  +55.319 -160.521 +0006.4 20050101 20191111


722393 99999 HIGH ISLAND A489B             US   LA       +28.200 -094.200 +0000.0 19880105 19930330
722394 99999 SHIP SHOAL B224A              US   LA       +28.500 -091.300 +0032.0 19870713 20050217
722395 99999 GRAND ISLE B95                US   LA       +28.500 -090.120 +0001.0 19761102 19830609
722396 99999 EUGENE ISLAND                 US   LA       +28.250 -091.833 +0001.0 19770827 19830609
722397 99999 SHIP SHOAL PLATFORM           US   LA       +28.680 -091.220 +0018.0 19780401 19851230
722398 99999 SOUTH MARSH ISLAND            US   LA       +28.300 -091.980 +0001.0 19840607 20030304
722399 99999 ZAPATA-YORKTOWNTLAT           US            +27.417 -094.417 +0017.0 19850201 20110816
722400 03937 LAKE CHARLES REGIONAL AIRPORT US   LA KLCH  +30.125 -093.228 +0002.7 19420502 20191111
722403 12968 SALT POINT                    US   LA KP92  +29.562 -091.526 +0001.2 20060413 20191111
722403 99999 SALT POINT                    US   LA KP92  +29.560 -091.533 +0000.0 19850208 20050923


740790 99999 THOMPSON AIRPORT              CA            +55.800 -097.867 +0222.0 19730101 19770630
740800 99999 MACKAR INLET                  CA            +68.300 -085.683 +0399.0 19730101 19770802
740810 99999 HALL BEACH AIRPORT            CA            +68.783 -081.250 +0008.0 19730101 19770630
740820 99999 ALERT                         CA            +82.500 -062.333 +0067.0 19510101 19770630
740900 99999 CYLDE AIRPORT     &           CA            +70.450 -068.550 +0002.0 19450501 19770630
740910 99999 LONGSTAFF BLUFF               CA            +68.950 -075.300 +0159.0 19730101 19770630
740920 99999 DEWAR LAKES                   CA            +68.650 -071.233 +0515.0 19730101 19770707
740930 99999 CAPE HOOPER       &           CA            +68.433 -066.783 +0396.0 19730101 19770731
740940 99999 CAPE DYER AIRPORT             CA            +66.583 -061.617 +0393.0 19730101 19770809
740950 99999 POND INLET AIRPORT            CA            +72.667 -078.000 +0059.0 19750109 19770630


873050 99999 JACHAL                        AR      SAMJ  -30.250 -068.750 +1165.0 19730101 20170302
873110 99999 SAN JUAN                      AR      SANU  -31.571 -068.418 +0597.1 19730101 20191110
873120 99999 SAN JUAN SOUTH                AR            -31.583 -068.533 +0630.0 19390201 19661029
873200 99999 CHAMICAL AERO                 AR            -30.367 -066.283 +0467.0 19730102 20191110
873205 99999 CHAMICAL                      AR      SACT  -30.345 -066.294 +0458.1 19940719 20001101
873220 99999 CHEPES                        AR      SACP  -31.333 -066.600 +0658.0 19730101 20170302
873280 99999 VILLA DOLORES                 AR      SAOD  -31.945 -065.146 +0583.7 19730101 20191110
873290 99999 VALLE DEL CONLARA             AR      SAOS  -32.385 -065.187 +0616.0 20040803 20190531
873360 99999 LA CUMBRE                     AR            -31.000 -064.533 +1138.0 19740813 19750513
873440 99999 AMBROSIO L V TARAVELLA        AR      SACO  -31.324 -064.208 +0488.9 19390201 20191110


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
vsensors_df.to_csv(path_or_buf="./data/static_data.csv", index=True)

In [13]:
vsensors_df.head()

min_lat    max_lat     min_lon     max_lon  x   y  center_lat  \
0  37.822662  37.826210 -122.536985 -122.532493  0  34   37.824436   
1  37.826210  37.829757 -122.536985 -122.532493  0  35   37.827984   
2  37.829757  37.833305 -122.536985 -122.532493  0  36   37.831531   
3  37.833305  37.836852 -122.536985 -122.532493  0  37   37.835079   
4  37.836852  37.840400 -122.536985 -122.532493  0  38   37.838626   

   center_lon  in_water  ndvi  elevation                             NN_list  \
0 -122.534739     False -2000         17  [18753, 5642, 21203, 19297, 18907]   
1 -122.534739     False -2000          0  [18753, 5642, 21203, 19297, 18907]   
2 -122.534739     False -2000          0  [18753, 5642, 21203, 19297, 18907]   
3 -122.534739     False  5159         55  [18753, 5642, 21203, 19297, 18907]   
4 -122.534739     False  7053        132  [18753, 5642, 18907, 21203, 19297]   

     closest_epa  closest_NOAA  
0  San Francisco         99999  
1  San Francisco         99999  
2  San Francisco         99999  
3  San Francisco         99999  
4  San Francisco         99999

In [14]:
NOAA_df

usaf  wban_number                                     descriptor  \
19770  724930        23230   METRO OAKLAND INTL AIRPORT    US   CA KOAK     
27285  994016        99999   SAN FRANCISCO                 US   CA          
27302  994033        99999   ALAMEDA                       US   CA          
27305  994036        99999   RICHMOND                      US   CA          
27987  997734        99999   TIBURON PIER                  US   CA          
28152  998197        99999   OAKLAND MIDDLE HARBOR MET     US   CA          
28313  998476        99999   OAKLAND (BERTH 34)            US   CA          
28314  998477        99999   RICHMOND (POINT POTRERO)      US   CA          
28316  998479        99999   SAN FRANCISCO (PIER 1)        US   CA          
28333  998496        99999   OAKLAND                       US   CA          
29032  999999        23272   DOWNTOWN                      US   CA          

          lat      lon   elev_m begin_date  end_date  
19770  37.721 -122.221  +0001.8   19430101  20191111  
27285  37.807 -122.465  +0002.0   20080101  20191110  
27302  37.772 -122.298  +0002.0   20080101  20191110  
27305  37.928 -122.400  +0005.6   20080101  20191110  
27987  37.920 -122.450  +0003.0   20080101  20191110  
28152  37.800 -122.317  +0007.0   20080721  20191110  
28313  37.811 -122.333  +0010.0   20130101  20191110  
28314  37.906 -122.365  +0010.0   20130101  20191110  
28316  37.798 -122.393  +0010.0   20130101  20191110  
28333  37.795 -122.288  +0004.0   20130101  20191110  
29032  37.771 -122.427  +0045.7   19450101  20191110

DO I NEED THESE?
import numpy as np
import json
from geopy import distance

from time import sleep
import shapely.geometry
import pyproj
import geopandas as gpd
from matplotlib import pyplot as plt
from shapely.geometry import Point
import datetime
from datetime import date, timedelta
from os import path
import statistics
import boto3
import s3fs
import sys
from fastparquet import ParquetFile
from sklearn import linear_model
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.preprocessing import StandardScaler
import gmplot
import math
import time
from collections import defaultdict

import warnings
warnings.filterwarnings('ignore')

pd.set_option('display.max_columns', 500)

csv built that has:
    virtual sensor grid fields
    elevation
    ocean yes/no
    closest epa/noaa
    NDVI
    closest 5 sensors to virtual sensor grid
static_data.csv
    
each hour, build dataframe from csv adding:
    previous 7 days NOAA wind readings -- (lookup by x,y in csv)
    previous 7 EPA readings -- (lookup by x,y in csv)
    getData() for 7 days -- previous 7 days humidity/temp from nearest PA sensor (lookup by sensor_id in csv, top 5)
    ---- grab the point in time that falls on the hour, so 24 * 7 = 168 time point observations going into model
X_data_df
    
from model:
    get predicted 168 PM2.5 values for each virtual sensor
    average the 168 values down to one
    sort highest to lowest readings
most_polluted.csv
    
Freshest possible:
    NOAA wind
    EPA readings (hourly)
    humidity & temp from nearest PA sensor
    
Occasional refresh:
    NDVI
    closest sensor to virtual sensor grid
    
Never refresh:
    elevation
    ocean yes/no
    closest epa/noaa to virtual sensor grid 
    


